In [1]:
%config IPCompleter.greedy=True
import re
import json
from collections import defaultdict
from tqdm import tqdm_notebook as tqdm
from elasticsearch import Elasticsearch
from elasticsearch.helpers import parallel_bulk
from sklearn.feature_extraction.text import CountVectorizer
import requests
from time import time
import time

import base64
import xmltodict

/usr/lib/python3/dist-packages/requests/__init__.py:80: RequestsDependencyWarning: urllib3 (1.25.6) or chardet (3.0.4) doesn't match a supported version!
  RequestsDependencyWarning)


In [2]:
es = Elasticsearch([{'host': 'localhost', 'port': 9200, 'timeout': 360, 'maxsize': 25}])

In [4]:
documents_by_id = {}
#es.indices.delete(index='myandex')
es.indices.create(index='myandex')

{'acknowledged': True, 'index': 'myandex', 'shards_acknowledged': True}

In [7]:
bytes_average = 12833

def processFile(i):
    prefix = '../byweb_for_course/byweb.'
    suffix = '.xml'
    filename = prefix + str(i) + suffix
    with open(filename, 'rb') as f:
        decoded = f.read().decode('cp1251')
        xmldict = xmltodict.parse(decoded)
        for doc in tqdm(xmldict['romip:dataset']['document']):
            try:
                docID = doc['docID']
                documents_by_id[docID] = {}
                url = base64.b64decode(doc['docURL']).decode('cp1251')
                content = base64.b64decode(doc['content']['#text']).decode('cp1251')
                documents_by_id[docID]['url'] = url
                documents_by_id[docID]['bytesVar'] = 1 / (abs(bytes_average - len(content.encode('utf-8'))) ** 2 + 1e-4)
                documents_by_id[docID]['content'] = content
            except Exception as e:
                print(e)

In [8]:
for i in range(10):
    processFile(i)

In [9]:
settings_final = {
    'mappings': {
        'properties': {
            'url': {
                'type': 'text'
            },
            'content': {
                'type': 'text'
            }
        }
    },
    "settings": {
    "analysis": {
      "analyzer": {
        "my_custom_analyzer": {
          "type":      "custom", 
          "tokenizer": "standard",
          "char_filter": [
            "html_strip",
            "yont"
          ],
          "filter": [
            "lowercase",
            "asciifolding",
            "russian_snow",
            "english_snow"
          ]
        }
      },
        'char_filter': {
                'yont': {
                    'type': 'mapping',
                    'mappings': [
                        'ё => е',
                        'Ё => Е'
                    ]
                }
            },
    'filter': {
            'stop_words': {
                'type': 'stop',
                'stopwords': [
                ]
            },
            'russian_snow': {
                'type': 'snowball',
                'language': 'russian'
            },
            'english_snow': {
                'type': 'snowball',
                'language': 'english'
            }
     }
    }
  }
}

In [10]:
def recreate_index():
    es.indices.delete(index='myandex')
    es.indices.create(index='myandex', body=settings_final)

In [51]:
recreate_index()

In [41]:
def check_analyzer(analyzer, text):
    body = analyzer
    body['text'] = text
    
    tokens = es.indices.analyze(index='myandex', body=body)['tokens']
    tokens = [token_info['token'] for token_info in tokens]
    return tokens

In [44]:
analyzer = {
    'analyzer': 'my_custom_analyzer'
}

check_analyzer(analyzer, '<meta http-equiv="Content-Type" content="text/html; charset=windows-1251"> bla bla русский countable текст Ёшкин кот')

['bla', 'bla', 'русск', 'countabl', 'текст', 'ешкин', 'кот']

In [12]:
def create_es_action(index, doc_id, document):
    return {
        '_index': index,
        '_id': doc_id,
        '_source': document
    }

In [13]:
def es_actions_generator():
    for doc_id, doc in tqdm(documents_by_id.items()):
        yield create_es_action('myandex', doc_id, doc)

In [14]:
start = time.time()
for ok, result in parallel_bulk(es, es_actions_generator(), queue_size=4, thread_count=4, chunk_size=1000):
    if not ok:
        print(result)
end = time.time()
print(f"Time on index creation: {time.strftime('%H:%M:%S.%l', time.gmtime(end - start))}")
print(f"In seconds: {end - start}")


Time on index creation: 00:56:13.12
In seconds: 3373.236542701721


In [14]:
def search(query, *args):
    pretty_print_result(es.search(index='myandex', body=query, size=20), args)
    # note that size set to 20 just because default value is 10 and we know that we have 12 docs and 10 < 12 < 20

def raw_search(query):
    search_result = es.search(index='myandex', body=query, size=20)['hits']
    return [(hit['_id'], hit['_score']) for hit in search_result['hits']]
    
def pretty_print_result(search_result, fields=[]):
    # fields is a list of fields names which we want to be printed
    res = search_result['hits']
    print(f'Total documents: {res["total"]["value"]}')
    for hit in res['hits'][:6]:
        print(f'Doc {hit["_id"]}, score is {hit["_score"]}')
        for field in fields:
            print(f'{field}: {hit["_source"][field]}')
                  
def get_doc_by_id(doc_id):
    return es.get(index='myandex', id=doc_id)['_source']

In [48]:
def get_query(query):
    return {
    'query': {
        'bool': {
            'should': {
                'match': {
                    'content': query
                }
            }
        }
    }
    }

q = get_query('<meta http-equiv="Content-Type" content="text/html; charset=windows-1251">')
search(q)
raw_search(q)

Total documents: 10000
Doc 658547, score is 1.073217
Doc 1075085, score is 1.0685503
Doc 571929, score is 1.0613596
Doc 1412110, score is 1.0609068
Doc 1132394, score is 1.0604091
Doc 1128759, score is 1.0576842


[('658547', 1.073217),
 ('1075085', 1.0685503),
 ('571929', 1.0613596),
 ('1412110', 1.0609068),
 ('1132394', 1.0604091),
 ('1128759', 1.0576842),
 ('1003757', 1.0573583),
 ('816437', 1.0573583),
 ('1004958', 1.0553992),
 ('1170976', 1.0553992),
 ('998704', 1.05511),
 ('1170977', 1.0550836),
 ('270685', 1.0531932),
 ('413190', 1.0531932),
 ('1227259', 1.0386738),
 ('825463', 1.0386703),
 ('826242', 1.0386703),
 ('363995', 1.0380677),
 ('649409', 1.0380677),
 ('90682', 1.0378789)]

In [15]:
def print_index_size(index): 
    print(f"Size of index: {es.indices.stats(index)['_all']['primaries']['store']['size_in_bytes'] / 2 ** 30} GB")

In [18]:
print_index_size('myandex')

Size of index: 4.730848075821996 GB


In [57]:
def load_queries_and_relevance():
    relevance = defaultdict(dict)
    filename = '../relevant_table_2009.xml'
    with open(filename, 'rb') as f:
        xmldict = xmltodict.parse(f.read())
        for task in tqdm(xmldict['taskDocumentMatrix']['task']):
            task_rel = {}
            has_vital = False
            for doc in task['document']:
                if doc['@relevance'] == 'vital':
                    has_vital = True
                task_rel[doc['@id']] = doc['@relevance']
            if has_vital:
                relevance[task['@id']] = task_rel
    filename = '../web2008_adhoc.xml'
    with open(filename, 'rb') as f:
        xmldict = xmltodict.parse(f.read())
        for task in tqdm(xmldict['task-set']['task']):
            if task['@id'] in relevance:
                relevance[task['@id']]['querytext'] = task['querytext']
    return relevance

In [58]:
relevance = load_queries_and_relevance()

In [46]:
def get_number_of_correct_out_of_k(results, task_relevance, k):
    return sum([1 if res[0] in task_relevance and task_relevance[res[0]] == 'vital' else 0 for res in results[:k]])

def measure_performance():    
    Q = len(relevance)
    pq = 0
    rq = 0
    prq = 0
    mapq = 0
    for task in relevance.keys():
        sk = 0
        task_relevance = relevance[task]
        results = raw_search(get_query(task_relevance['querytext']))
        #if len(results) < 20:
        #    print("WARNING LESS 20")
        sk = get_number_of_correct_out_of_k(results, task_relevance, 20)
        pq += sk / 20
        relevant_size = len(['vital' for value in task_relevance.values() if value == 'vital'])
        rq += sk / relevant_size
        prq += get_number_of_correct_out_of_k(results, task_relevance, relevant_size) / relevant_size
        mapk = 0
        for k in range(1, 21):
            mapk += get_number_of_correct_out_of_k(results, task_relevance, k) / k
        mapk /= 20
        mapq += mapk
    print(f"p@20: {pq / Q}")
    print(f"r@20: {rq / Q}")
    print(f"p@R(q): {prq / Q}")
    print(f"map@20(q): {mapq / Q}")

In [49]:
measure_performance()

ZeroDivisionError: division by zero

In [29]:
def get_empty_query():
    return {
    'query': {
        'bool': {
            'should': {
                'match': {
                    'content': ''
                }
            }
        }
    }
    }

q = get_empty_query()
search(q)
raw_search(q)

Total documents: 0


[]

In [28]:
import networkx as nx

In [29]:
def augment(hash, nodes, edges, line):
    n = line.split(';')
    nodes.append(n[0].strip())
    hash[n[0].strip()] = True
    for i in range(1, len(n)):
        edges.append((n[0], n[i].strip()))

In [30]:
h = defaultdict(bool)
nodes, edges = [], []
with open("../hw_1/graph.csv", 'r', encoding='cp1251') as f:
    [augment(h, nodes, edges, line) for line in f.readlines()]
G = nx.DiGraph()
for (u, v) in edges:
    if h[u]:
        G.add_edge(u, v)
pagerank = nx.pagerank(G)


In [31]:
def es_action_generator_with_static_info():
    for doc_id, doc in tqdm(documents_by_id.items()):
        doc['pagerank'] = pagerank.get(doc['url'], 0)
        yield create_es_action('myandex', doc_id, doc)

In [50]:
settings_final = {
    'mappings': {
        'properties': {
            'url': {
                'type': 'text'
            },
            'content': {
                'type': 'text'
            },
            'pagerank': {
                    'type': 'rank_feature'
                },
            'bytesVar': {
                    'type': 'rank_feature'
            }
        }
    },
    "settings": {
    "analysis": {
      "analyzer": {
        "my_custom_analyzer": {
          "type":      "custom", 
          "tokenizer": "standard",
          "char_filter": [
            "html_strip",
            "yont"
          ],
          "filter": [
            "lowercase",
            "asciifolding",
            "russian_snow",
            "english_snow"
          ]
        }
      },
        'char_filter': {
                'yont': {
                    'type': 'mapping',
                    'mappings': [
                        'ё => е',
                        'Ё => Е'
                    ]
                }
            },
    'filter': {
            'stop_words': {
                'type': 'stop',
                'stopwords': [
                ]
            },
            'russian_snow': {
                'type': 'snowball',
                'language': 'russian'
            },
            'english_snow': {
                'type': 'snowball',
                'language': 'english'
            }
     }
    }
  }
}

In [52]:
start = time.time()
for ok, result in parallel_bulk(es, es_action_generator_with_static_info(), queue_size=4, thread_count=4, chunk_size=1000):
    if not ok:
        print(result)
end = time.time()
print(f"Time on index creation: {time.strftime('%H:%M:%S.%l', time.gmtime(end - start))}")
print(f"In seconds: {end - start}")

BulkIndexError: ('96 document(s) failed to index.', [{'index': {'_index': 'myandex', '_type': '_doc', '_id': '54', 'status': 400, 'error': {'type': 'mapper_parsing_exception', 'reason': "failed to parse field [pagerank] of type [rank_feature] in document with id '54'. Preview of field's value: '0'", 'caused_by': {'type': 'illegal_argument_exception', 'reason': 'featureValue must be a positive normal float, got: 0.0for feature pagerank on field _feature which is less than the minimum positive normal float: 1.17549435E-38'}}, 'data': {'url': 'http://brest.linux.by/forum/index.php?action=vthread&forum=8&topic=136&page=2', 'bytesVar': 4.084803244661288e-11, 'content': '<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN">\n<html>\n<HEAD><title>Форумы BLUG :: sfgwg</title>\n<meta http-equiv="content-type" content="text/html;charset=windows-1251">\n<META NAME="Description" CONTENT="Free/GPL universal PHP-based forums engine for real minimalists. Small, simple, fast and powerful. Fi

In [53]:
print_index_size('myandex')

Size of index: 6.034386842511594 GB


In [54]:
def get_query_with_static_info(query, pagerank_weight, bytes_var_weight):
    return {
            'query': {
                'bool': {
                    'should': [
                        {
                            'match': {
                                'content': query
                            }
                        },
                        {
                            'rank_feature': {
                                'field': 'pagerank',
                                'boost': pagerank_weight,
                            },
                        },
                        {
                            'rank_feature': {
                                'field': 'bytesVar',
                                'boost': bytes_var_weight
                            },
                        }
                    ]
                }
            }
        }

In [55]:
def measure_performance(pagerank_weight, bytes_var_weight):    
    Q = len(relevance)
    pq = 0
    rq = 0
    prq = 0
    mapq = 0
    for task in relevance.keys():
        sk = 0
        task_relevance = relevance[task]
        results = raw_search(get_query_with_static_info(task_relevance['querytext'], pagerank_weight, bytes_var_weight))
        #if len(results) < 20:
        #    print("WARNING LESS 20")
        sk = get_number_of_correct_out_of_k(results, task_relevance, 20)
        pq += sk / 20
        relevant_size = len(['vital' for value in task_relevance.values() if value == 'vital'])
        rq += sk / relevant_size
        prq += get_number_of_correct_out_of_k(results, task_relevance, relevant_size) / relevant_size
        mapk = 0
        for k in range(1, 21):
            mapk += get_number_of_correct_out_of_k(results, task_relevance, k) / k
        mapk /= 20
        mapq += mapk
    print(f"p@20: {pq / Q}")
    print(f"r@20: {rq / Q}")
    print(f"p@R(q): {prq / Q}")
    print(f"map@20(q): {mapq / Q}")

In [59]:
for pagerank_weight in [0.3, 0.5, 0.7]:
    for bytes_var_weight in [0.3, 0.5, 0.7]:
        print('Pagerank weight: ' + str(pagerank_weight))
        print('Inverse bytes variance weigth: ' + str(bytes_var_weight))
        measure_performance(pagerank_weight, bytes_var_weight)

Pagerank weight: 0.3
Inverse bytes variance weigth: 0.3
p@20: 0.31121212121212116
r@20: 0.20476080518398967
p@R(q): 0.1709616510348964
map@20(q): 0.37104382326089375
Pagerank weight: 0.3
Inverse bytes variance weigth: 0.5
p@20: 0.30939393939393933
r@20: 0.20413421633401072
p@R(q): 0.17048756763154055
map@20(q): 0.36729740638982844
Pagerank weight: 0.3
Inverse bytes variance weigth: 0.7
p@20: 0.3074747474747475
r@20: 0.20253078965965546
p@R(q): 0.16961615857211879
map@20(q): 0.3646992007381938
Pagerank weight: 0.5
Inverse bytes variance weigth: 0.3
p@20: 0.31090909090909075
r@20: 0.20424063933302278
p@R(q): 0.1709855220437559
map@20(q): 0.37069969779710377
Pagerank weight: 0.5
Inverse bytes variance weigth: 0.5
p@20: 0.3075757575757575
r@20: 0.20283527087581793
p@R(q): 0.16988417418468924
map@20(q): 0.36773866763047275
Pagerank weight: 0.5
Inverse bytes variance weigth: 0.7
p@20: 0.3065656565656565
r@20: 0.20186350109890325
p@R(q): 0.16912561535065054
map@20(q): 0.3655607132662085
Pager